In [1]:
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
import torch
from torch import nn
from torch.utils.data import TensorDataset, DataLoader, random_split
from torch.optim import Adam
from torch.nn.functional import mse_loss
from torch.optim.lr_scheduler import ReduceLROnPlateau
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler, OneHotEncoder
from sklearn.compose import ColumnTransformer
from scipy.stats import norm
import gym
from gym import spaces
from stable_baselines3 import PPO
import talib as ta

import warnings
warnings.filterwarnings("ignore")

## Technical Indicators

In [2]:
class TechnicalIndicators:
    def __init__(self, data):
        self.data = data

    def add_momentum_indicators(self):
        self.data['RSI'] = ta.RSI(self.data['Close'], timeperiod=14)
        self.data['MACD'], self.data['MACD_signal'], self.data['MACD_hist'] = ta.MACD(self.data['Close'], fastperiod=12, slowperiod=26, signalperiod=9)
        self.data['Stoch_k'], self.data['Stoch_d'] = ta.STOCH(self.data['High'], self.data['Low'], self.data['Close'],
                                                              fastk_period=14, slowk_period=3, slowd_period=3)

    def add_volume_indicators(self):
        self.data['OBV'] = ta.OBV(self.data['Close'], self.data['Volume'])

    def add_volatility_indicators(self):
        self.data['Upper_BB'], self.data['Middle_BB'], self.data['Lower_BB'] = ta.BBANDS(self.data['Close'], timeperiod=20)
        self.data['ATR_1'] = ta.ATR(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=1)
        self.data['ATR_2'] = ta.ATR(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=2)
        self.data['ATR_5'] = ta.ATR(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=5)
        self.data['ATR_10'] = ta.ATR(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=10)
        self.data['ATR_20'] = ta.ATR(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=20)

    def add_trend_indicators(self):
        self.data['ADX'] = ta.ADX(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=14)
        self.data['+DI'] = ta.PLUS_DI(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=14)
        self.data['-DI'] = ta.MINUS_DI(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=14)
        self.data['CCI'] = ta.CCI(self.data['High'], self.data['Low'], self.data['Close'], timeperiod=5)

    def add_other_indicators(self):
        self.data['DLR'] = np.log(self.data['Close'] / self.data['Close'].shift(1))
        self.data['TWAP'] = self.data['Close'].expanding().mean()
        self.data['VWAP'] = (self.data['Volume'] * (self.data['High'] + self.data['Low']) / 2).cumsum() / self.data['Volume'].cumsum()

    def add_all_indicators(self):
        self.add_momentum_indicators()
        self.add_volume_indicators()
        self.add_volatility_indicators()
        self.add_trend_indicators()
        self.add_other_indicators()
        return self.data

## Adding Technical Indicators to the Dataframe

In [3]:
# data = pd.read_csv('/Users/proddy/Blockhouse/Blockhouse-ML/xnas-itch-20230703.tbbo.csv')
data = pd.read_csv('/Users/priyankasahoo/Downloads/xnas-itch-20230703.tbbo.csv')

# Preprocessing to create necessary columns
data['price']=data['price']/1e9
data['bid_px_00']=data['bid_px_00']/1e9
data['ask_px_00']=data['ask_px_00']/1e9

data['Close'] = data['price']
data['Volume'] = data['size']
data['High'] = data[['bid_px_00', 'ask_px_00']].max(axis=1)
data['Low'] = data[['bid_px_00', 'ask_px_00']].min(axis=1)
data['Open'] = data['Close'].shift(1).fillna(data['Close'])


ti = TechnicalIndicators(data)
df_with_indicators = ti.add_all_indicators()
market_features_df = df_with_indicators[35:]
market_features_df

ts_recv             ts_event  rtype  publisher_id  \
35     1688371214386057385  1688371214385893078      1             2   
36     1688371214386063777  1688371214385899379      1             2   
37     1688371215804852019  1688371215804687301      1             2   
38     1688371219671476629  1688371219671312224      1             2   
39     1688371223368835585  1688371223368671235      1             2   
...                    ...                  ...    ...           ...   
59266  1688417954514485218  1688417954514320323      1             2   
59267  1688417961020718430  1688417961020553920      1             2   
59268  1688417973297905504  1688417973297741235      1             2   
59269  1688417996889779362  1688417996889614660      1             2   
59270  1688417998907430616  1688417998907265922      1             2   

       instrument_id action side  depth   price  size  ...     ATR_5  \
35                32      T    N      0  194.05    50  ...  0.098615   
36                32      T    N      0  194.05    50  ...  0.138892   
37                32      T    B      0  194.21    10  ...  0.153114   
38                32      T    N      0  194.14    10  ...  0.164491   
39                32      T    B      0  194.13    10  ...  0.159593   
...              ...    ...  ...    ...     ...   ...  ...       ...   
59266             32      T    B      0  192.44     6  ...  0.031258   
59267             32      T    B      0  192.44     1  ...  0.033006   
59268             32      T    A      0  192.40     5  ...  0.038405   
59269             32      T    B      0  192.45     3  ...  0.040724   
59270             32      T    B      0  192.45     3  ...  0.042579   

         ATR_10    ATR_20        ADX        +DI       -DI         CCI  \
35     0.075141  0.072403  97.257397  30.435801  0.196362  166.666667   
36     0.097627  0.083783  97.361721  22.989295  0.148320   83.333333   
37     0.108864  0.090094  97.458593  19.409454  0.125224   79.268293   
38     0.118978  0.096089  97.548546  16.622008  0.107240   -3.205128   
39     0.121080  0.098285  97.632074  15.068361  0.097216 -113.095238   
...         ...       ...        ...        ...       ...         ...   
59266  0.028636  0.027592  15.474528   6.612534  3.765166  118.055556   
59267  0.029772  0.028212  16.329018   5.953254  3.389772   83.333333   
59268  0.032795  0.029802  19.013869   9.751295  2.919558   12.820513   
59269  0.034515  0.030812  21.506945   8.671762  2.596344  100.000000   
59270  0.036064  0.031771  23.821945   7.748024  2.319775   83.333333   

            DLR        TWAP        VWAP  
35     0.000000  194.020000  194.021894  
36     0.000000  194.020811  194.025188  
37     0.000824  194.025789  194.025596  
38    -0.000360  194.028718  194.025873  
39    -0.000052  194.031250  194.026071  
...         ...         ...         ...  
59266  0.000208  192.701135  192.722211  
59267  0.000000  192.701131  192.722211  
59268 -0.000208  192.701125  192.722211  
59269  0.000260  192.701121  192.722211  
59270  0.000000  192.701117  192.722211  

[59236 rows x 47 columns]

## Dropping redundant features and encoding columns

In [4]:
market_features_df = market_features_df.drop(['rtype', 'publisher_id', 'instrument_id', 'action', 'depth', 'sequence'], axis=1)
side_mapping = {'A': 1, 'B': 2, 'N': 0}
market_features_df['side'] = market_features_df['side'].map(side_mapping)

flag_mapping = {130: 1, 128: 2, 0: 0}
market_features_df['flags'] = market_features_df['flags'].map(flag_mapping)
market_features_df


ts_recv             ts_event  side   price  size  flags  \
35     1688371214386057385  1688371214385893078     0  194.05    50      1   
36     1688371214386063777  1688371214385899379     0  194.05    50      1   
37     1688371215804852019  1688371215804687301     2  194.21    10      1   
38     1688371219671476629  1688371219671312224     0  194.14    10      1   
39     1688371223368835585  1688371223368671235     2  194.13    10      1   
...                    ...                  ...   ...     ...   ...    ...   
59266  1688417954514485218  1688417954514320323     2  192.44     6      1   
59267  1688417961020718430  1688417961020553920     2  192.44     1      1   
59268  1688417973297905504  1688417973297741235     1  192.40     5      1   
59269  1688417996889779362  1688417996889614660     2  192.45     3      1   
59270  1688417998907430616  1688417998907265922     2  192.45     3      1   

       ts_in_delta  bid_px_00  ask_px_00  bid_sz_00  ...     ATR_5    ATR_10  \
35          164307      194.0     194.30       3101  ...  0.098615  0.075141   
36          164398      194.0     194.30       3101  ...  0.138892  0.097627   
37          164718      194.0     194.21       3101  ...  0.153114  0.108864   
38          164405      194.0     194.16       3101  ...  0.164491  0.118978   
39          164350      194.0     194.13       3101  ...  0.159593  0.121080   
...            ...        ...        ...        ...  ...       ...       ...   
59266       164895      192.4     192.44         40  ...  0.031258  0.028636   
59267       164510      192.4     192.44         40  ...  0.033006  0.029772   
59268       164269      192.4     192.46         40  ...  0.038405  0.032795   
59269       164702      192.4     192.45         35  ...  0.040724  0.034515   
59270       164694      192.4     192.45         35  ...  0.042579  0.036064   

         ATR_20        ADX        +DI       -DI         CCI       DLR  \
35     0.072403  97.257397  30.435801  0.196362  166.666667  0.000000   
36     0.083783  97.361721  22.989295  0.148320   83.333333  0.000000   
37     0.090094  97.458593  19.409454  0.125224   79.268293  0.000824   
38     0.096089  97.548546  16.622008  0.107240   -3.205128 -0.000360   
39     0.098285  97.632074  15.068361  0.097216 -113.095238 -0.000052   
...         ...        ...        ...       ...         ...       ...   
59266  0.027592  15.474528   6.612534  3.765166  118.055556  0.000208   
59267  0.028212  16.329018   5.953254  3.389772   83.333333  0.000000   
59268  0.029802  19.013869   9.751295  2.919558   12.820513 -0.000208   
59269  0.030812  21.506945   8.671762  2.596344  100.000000  0.000260   
59270  0.031771  23.821945   7.748024  2.319775   83.333333  0.000000   

             TWAP        VWAP  
35     194.020000  194.021894  
36     194.020811  194.025188  
37     194.025789  194.025596  
38     194.028718  194.025873  
39     194.031250  194.026071  
...           ...         ...  
59266  192.701135  192.722211  
59267  192.701131  192.722211  
59268  192.701125  192.722211  
59269  192.701121  192.722211  
59270  192.701117  192.722211  

[59236 rows x 41 columns]

In [5]:
# Selecting relevant columns from the market features DataFrame
relevant_data = market_features_df[['price', 'side', 'flags', 'bid_px_00', 'ask_px_00', 'RSI', 'MACD', 'ATR_5', 'ATR_10', 'ATR_20', 'CCI', 'DLR', 'TWAP']]

# Initializing lists to hold input sequences and corresponding target prices
input_sequences = []
output_prices = []

# Defining the window size for sequence creation
window_size = 5

# Looping through the DataFrame to create sequences
for i in range(len(relevant_data) - window_size):
    # Flatten the sequence data to include all selected features for each step in one flat sequence
    sequence = relevant_data.iloc[i:i+window_size].to_numpy().flatten()
    input_sequences.append(sequence)
    # The target price is the 'price' value after the end of the sequence
    output_prices.append(relevant_data.iloc[i + window_size]['price'])

# Creating column names for the DataFrame
column_names = []
for i in range(window_size):
    for feature in ['price', 'side', 'flags', 'bid_px_00', 'ask_px_00', 'RSI', 'MACD', 'ATR_5', 'ATR_10', 'ATR_20', 'CCI', 'DLR', 'TWAP']:
        column_names.append(f"{feature}_{i+1}")

# Creating a DataFrame with the input sequences and their corresponding target prices
sequence_data_with_features = pd.DataFrame(input_sequences, columns=column_names)
sequence_data_with_features['Next_Price'] = output_prices

sequence_data_with_features.head()


price_1  side_1  flags_1  bid_px_00_1  ask_px_00_1      RSI_1    MACD_1  \
0   194.05     0.0      1.0        194.0       194.30  54.544543  0.006271   
1   194.05     0.0      1.0        194.0       194.30  54.544543  0.007108   
2   194.21     2.0      1.0        194.0       194.21  85.890753  0.020446   
3   194.14     0.0      1.0        194.0       194.16  64.827662  0.025079   
4   194.13     2.0      1.0        194.0       194.13  62.470772  0.027625   

    ATR_5_1  ATR_10_1  ATR_20_1  ...  ask_px_00_5      RSI_5    MACD_5  \
0  0.098615  0.075141  0.072403  ...       194.13  62.470772  0.027625   
1  0.138892  0.097627  0.083783  ...       194.13  62.470772  0.029305   
2  0.153114  0.108864  0.090094  ...       194.16  42.676806  0.021513   
3  0.164491  0.118978  0.096089  ...       194.16  41.392784  0.014365   
4  0.159593  0.121080  0.098285  ...       194.16  41.392784  0.008601   

    ATR_5_5  ATR_10_5  ATR_20_5       CCI_5     DLR_5      TWAP_5  Next_Price  
0  0.159593  0.121080  0.098285 -113.095238 -0.000052  194.031250      194.13  
1  0.151674  0.120972  0.099370  -64.102564  0.000000  194.033659      194.02  
2  0.151339  0.123875  0.101902 -113.425926 -0.000567  194.033333      194.01  
3  0.151071  0.126487  0.104307  -90.909091 -0.000052  194.032791      194.01  
4  0.150857  0.128839  0.106591  -61.224490  0.000000  194.032273      194.00  

[5 rows x 66 columns]

## Splitting Dataset into Train and Test sets

In [6]:
# Separating features and target prices from the DataFrame
features = sequence_data_with_features.drop(columns=['Next_Price']).values
prices = sequence_data_with_features['Next_Price'].values

# Normalize the features using StandardScaler
scaler = StandardScaler()
features_scaled = scaler.fit_transform(features)

# Convert to PyTorch tensors
features_tensor = torch.tensor(features_scaled, dtype=torch.float32)
prices_tensor = torch.tensor(prices, dtype=torch.float32).unsqueeze(1)  # Adding dimension for target

# Create dataset and split it
dataset = TensorDataset(features_tensor, prices_tensor)
train_size = int(0.8 * len(dataset))
test_size = len(dataset) - train_size
train_dataset, test_dataset = random_split(dataset, [train_size, test_size])

# Further split the train_dataset into training and validation sets
val_size = int(0.1 * len(train_dataset))
train_size = len(train_dataset) - val_size
train_dataset, val_dataset = random_split(train_dataset, [train_size, val_size])

# Creating DataLoaders for training, validation, and testing sets
batch_size = 64
train_loader = DataLoader(train_dataset, batch_size=batch_size, shuffle=True)
val_loader = DataLoader(val_dataset, batch_size=batch_size, shuffle=False)
test_loader = DataLoader(test_dataset, batch_size=batch_size, shuffle=False)

In [7]:
features_tensor.size()


torch.Size([59231, 65])

## Implementing Transformer Model

In [9]:
# Define the Transformer Model
class TransformerModel(nn.Module):

    def __init__(self, input_dim, num_heads, num_layers, dim_feedforward, output_dim):
        super(TransformerModel, self).__init__()
        self.positional_encoding = nn.Parameter(torch.zeros(1, input_dim))
        self.encoder_layers = nn.ModuleList([
            nn.TransformerEncoderLayer(
                d_model=input_dim, 
                nhead=num_heads, 
                dim_feedforward=dim_feedforward
            ) for _ in range(num_layers)
        ])
        self.layer_norm = nn.LayerNorm(input_dim)
        self.fc1 = nn.Linear(input_dim, dim_feedforward)
        # self.dropout = nn.Dropout(dropout_rate)
        self.activation = nn.ReLU() 
        self.fc_out = nn.Linear(dim_feedforward, output_dim)

    def forward(self, src):
        src += self.positional_encoding
        for layer in self.encoder_layers:
            src = layer(src)
        src = self.layer_norm(src)
        src = self.fc1(src)
        # src = self.dropout(src) 
        src = self.activation(src) 
        output = self.fc_out(src[:, -1, :])
        return output

# Instantiate the model
model = TransformerModel(
    input_dim=features_tensor.shape[1], 
    num_heads=5, 
    num_layers=3,  
    dim_feedforward=512,  
    output_dim=1
)
loss_fn = nn.MSELoss()
optimizer = torch.optim.Adam(model.parameters(), lr=0.001)


In [10]:
# Define the fine-tuning parameters
fine_tune_lr = 1e-5  
fine_tune_optimizer = torch.optim.Adam(model.parameters(), lr=fine_tune_lr)
fine_tune_scheduler = ReduceLROnPlateau(fine_tune_optimizer, 'min', patience=5, factor=0.5)

# Fine-tuning function
def fine_tune(dataloader, model, loss_fn, optimizer):
    model.train()
    total_loss = 0

    for batch, (X, y) in enumerate(dataloader):
        optimizer.zero_grad()
        pred = model(X.unsqueeze(0)) 
        loss = loss_fn(pred, y)
        loss.backward()
        optimizer.step()
        total_loss += loss.item()

    return total_loss / len(dataloader)

# Evaluate the model during fine-tuning
def evaluate_fine_tune(dataloader, model, loss_fn):
    model.eval()
    total_loss = 0
    with torch.no_grad():
        for batch, (X, y) in enumerate(dataloader):
            pred = model(X.unsqueeze(0))  # Ensure the input dimensions are correct
            loss = loss_fn(pred, y)
            total_loss += loss.item()
    return total_loss / len(dataloader)

# Fine-tuning loop
best_val_loss = float('inf')
patience_counter = 0

for epoch in range(40):  
    train_loss = fine_tune(train_loader, model, loss_fn, fine_tune_optimizer)
    val_loss = evaluate_fine_tune(val_loader, model, loss_fn)
    fine_tune_scheduler.step(val_loss)

    print(f'Epoch {epoch+1}, Train Loss: {train_loss:.4f}, Val Loss: {val_loss:.4f}')

    # Early stopping
    if val_loss < best_val_loss:
        best_val_loss = val_loss
        patience_counter = 0
    else:
        patience_counter += 1
        if patience_counter >= 3:
            print("Early stopping during fine-tuning")
            break


Epoch 1, Train Loss: 36648.2830, Val Loss: 36002.4332
Epoch 2, Train Loss: 35084.3865, Val Loss: 33958.3364
Epoch 3, Train Loss: 32775.7864, Val Loss: 31226.4910
Epoch 4, Train Loss: 29703.1695, Val Loss: 27709.0113
Epoch 5, Train Loss: 25924.6208, Val Loss: 23610.1404
Epoch 6, Train Loss: 21704.5224, Val Loss: 19237.9707
Epoch 7, Train Loss: 17347.0032, Val Loss: 14879.6032
Epoch 8, Train Loss: 13102.3469, Val Loss: 10790.6527
Epoch 9, Train Loss: 9233.2728, Val Loss: 7199.5507
Epoch 10, Train Loss: 5944.3928, Val Loss: 4290.4510
Epoch 11, Train Loss: 3386.0824, Val Loss: 2173.8910
Epoch 12, Train Loss: 1611.1569, Val Loss: 860.8230
Epoch 13, Train Loss: 596.7774, Val Loss: 225.3887
Epoch 14, Train Loss: 150.2606, Val Loss: 25.5276
Epoch 15, Train Loss: 22.5860, Val Loss: 0.3650
Epoch 16, Train Loss: 2.1951, Val Loss: 4.4900
Epoch 17, Train Loss: 0.7653, Val Loss: 5.7419
Epoch 18, Train Loss: 0.6917, Val Loss: 5.7943
Early stopping during fine-tuning


In [11]:
model

ModifiedTransformerModel(
  (encoder_layers): ModuleList(
    (0-2): 3 x TransformerEncoderLayer(
      (self_attn): MultiheadAttention(
        (out_proj): NonDynamicallyQuantizableLinear(in_features=65, out_features=65, bias=True)
      )
      (linear1): Linear(in_features=65, out_features=512, bias=True)
      (dropout): Dropout(p=0.1, inplace=False)
      (linear2): Linear(in_features=512, out_features=65, bias=True)
      (norm1): LayerNorm((65,), eps=1e-05, elementwise_affine=True)
      (norm2): LayerNorm((65,), eps=1e-05, elementwise_affine=True)
      (dropout1): Dropout(p=0.1, inplace=False)
      (dropout2): Dropout(p=0.1, inplace=False)
    )
  )
  (layer_norm): LayerNorm((65,), eps=1e-05, elementwise_affine=True)
  (fc1): Linear(in_features=65, out_features=512, bias=True)
  (activation): ReLU()
  (fc_out): Linear(in_features=512, out_features=1, bias=True)
)

## Integrating transformer model into the PPO Agent

In [13]:
import gym
from gym import spaces
import numpy as np
import pandas as pd
import torch
from torch import nn

class TradingEnvironment(gym.Env):
    metadata = {'render.modes': ['human']}

    def __init__(self, data, daily_trading_limit, transformer_model):
        super(TradingEnvironment, self).__init__()
        self.data = data
        self.transformer_model = transformer_model
        self.daily_trading_limit = daily_trading_limit
        self.current_step = 0
        
        self.transformer_features = ['price', 'side', 'flags', 'bid_px_00', 'ask_px_00', 'RSI', 'MACD', 'ATR_5', 'ATR_10', 'ATR_20', 'CCI', 'DLR', 'TWAP']
        self.state_columns = ['price', 'side', 'flags', 'bid_px_00', 'ask_px_00', 'RSI', 'MACD', 'ATR_5', 'ATR_10', 'ATR_20', 'CCI', 'DLR', 'TWAP', 'transformer']

        # Initialize balance, shares held, and total shares traded
        self.balance = 10_000_000.0  # $10 million
        self.shares_held = 0
        self.total_shares_traded = 0

        # Define action space: [Hold, Buy, Sell]
        self.action_space = spaces.Discrete(3)

        # Define observation space based on state columns
        self.observation_space = spaces.Box(low=-np.inf, high=np.inf, shape=(len(self.state_columns),), dtype=np.float32)

    def reset(self):
        self.current_step = 0
        self.balance = 10_000_000.0  # $10 million
        self.shares_held = 0
        self.total_shares_traded = 0
        self.cumulative_reward = 0
        self.trades = []
        return self._next_observation()

    def _next_observation(self):
        current_data = self.data[self.state_columns[:-1]].iloc[self.current_step].values

        if self.current_step > 5:
            features = self.data[self.transformer_features].iloc[self.current_step-6:self.current_step-1].to_numpy().flatten()
            
            n_features = 65  
            n_samples = len(features) // n_features 

            if len(features) % n_features != 0:
                raise ValueError("The total number of elements in 'features' is not a multiple of 65")

            features_reshaped = features.reshape(n_samples, n_features)

            # Scaling the features
            features_scaled = scaler.transform(features_reshaped)

            # Convert to tensor
            features_tensor = torch.tensor(features_scaled, dtype=torch.float32).unsqueeze(0)

            # Get prediction from the Transformer model
            self.transformer_model.eval() 
            with torch.no_grad():
                predicted_price = self.transformer_model(features_tensor)

            current_data = np.append(current_data, predicted_price[0][0].item())

        else:
            current_data = np.append(current_data, 0.0)

        return current_data

    def step(self, action):
        expected_price = self.data.iloc[self.current_step]['ask_px_00']
        actual_price = self.data.iloc[self.current_step]['price']
        transaction_time = self.data.iloc[self.current_step]['ts_in_delta']
        self._take_action(action)
        reward = 0
        
        if self.current_step >= len(self.data) - 1:
            self.current_step = 0
        
        if action != 0:
            transaction_cost= self._calculate_transaction_cost(self.data.iloc[self.current_step]['Volume'], 0.3, self.data['Volume'].mean())
            reward = self._calculate_reward(expected_price, actual_price, transaction_time, transaction_cost)
        
            self.cumulative_reward += reward
        
            if self.trades:
                self.trades[-1]['reward'] = reward
                self.trades[-1]['transaction_cost'] = transaction_cost
                self.trades[-1]['slippage'] = expected_price - actual_price
                self.trades[-1]['time_penalty'] = 100*transaction_time/1e9

        done = self.current_step == len(self.data) - 1
        obs = self._next_observation()

        info = {
            'step': self.current_step,
            'action': action,
            'price': actual_price,
            'shares': self.trades[-1]['shares'] if self.trades else 0
        }
        self.current_step += 1

        return obs, reward, done, info

    def _take_action(self, action):
        current_price = self.data.iloc[self.current_step]['Close']
        current_time = pd.to_datetime(self.data.iloc[self.current_step]['ts_event'])
        trade_info = {'step': self.current_step, 'timestamp': current_time, 'action': action, 'price': current_price, 'shares': 0, 'reward': 0, 'transaction_cost': 0, 'slippage': 0, 'time_penalty': 0}

        if action == 1 and self.total_shares_traded < self.daily_trading_limit:  # Buy
            shares_bought = (self.balance * np.random.uniform(0.001, 0.005)) // current_price
            self.balance -= shares_bought * current_price
            self.shares_held += shares_bought
            self.total_shares_traded += shares_bought
            trade_info['shares'] = shares_bought
            if(shares_bought > 0):
                self.trades.append(trade_info)
                
        elif action == 2 and self.total_shares_traded < self.daily_trading_limit:  # Sell
            shares_sold = min((self.balance * np.random.uniform(0.001, 0.005)) // current_price, self.shares_held)
            self.balance += shares_sold * current_price
            self.shares_held -= shares_sold
            self.total_shares_traded -= shares_sold
            trade_info['shares'] = shares_sold
            if(shares_sold > 0):
                self.trades.append(trade_info)

    def _calculate_reward(self, expected_price, actual_price, transaction_time, transaction_cost):
        slippage = expected_price - actual_price
        time_penalty = 100 * transaction_time / 1e9
        reward = -(slippage + time_penalty + transaction_cost)
        return reward
    
    def _calculate_transaction_cost(self, volume, volatility, daily_volume):
        return volatility * np.sqrt(volume / daily_volume)
    
    def run(self):
        self.reset()
        for _ in range(len(self.data)):
            self.step()
        return self.cumulative_reward, self.trades

    def render(self, mode='human', close=False):
        print(f'Step: {self.current_step}')
        print(f'Balance: {self.balance}')
        print(f'Shares held: {self.shares_held}')
        print(f'Total shares traded: {self.total_shares_traded}')
        print(f'Total portfolio value: {self.balance + self.shares_held * self.data.iloc[self.current_step]["Close"]}')
        print(f'Cumulative reward: {self.cumulative_reward}')
        self.print_trades()

    def print_trades(self):
        # download all trades in a pandas dataframe using .csv
        trades_df = pd.DataFrame(self.trades)
        # Save a csv
        trades_df.to_csv('/Users/priyankasahoo/Documents/trades_ppo.csv', index=False)
        for trade in self.trades:
            print(f"Step: {trade['step']}, Timestamp: {trade['timestamp']}, Action: {trade['action']}, Price: {trade['price']}, Shares: {trade['shares']}, Reward: {trade['reward']}, Transaction Cost: {trade['transaction_cost']}, Slippage: {trade['slippage']}, Time Penalty: {trade['time_penalty']}")


In [14]:
# Define the daily trading limit (total number of shares to trade per day)
daily_trading_limit = 1000

ticker = 'AAPL'  # Specify the ticker you want to trade
ticker_data = market_features_df[market_features_df['symbol'] == ticker]

env = TradingEnvironment(ticker_data, daily_trading_limit, model)  # Adjust window_size if needed


In [15]:
# Define the best hyperparameters
best_hyperparameters = {'learning_rate': 0.0009931989008886031,'n_steps': 512,'batch_size': 128, 'gamma': 0.9916829193042708,'clip_range': 0.21127653449387027,'n_epochs': 6} # type: ignore

# Create the RL model with the best hyperparameters
model = PPO('MlpPolicy', env, verbose=1, **best_hyperparameters)

# Train the model
model.learn(total_timesteps=10000)

# Save the model
model.save("/Users/priyankasahoo/Documents/trading_agent_ppo_transformer")

# Evaluate the model
obs = env.reset()
for _ in range(len(ticker_data)):
    action, _states = model.predict(obs)
    obs, rewards, done, info = env.step(action)
    if done:
        break

# Render the final state
env.render()

Using cpu device
Wrapping the env with a `Monitor` wrapper
Wrapping the env in a DummyVecEnv.
----------------------------
| time/              |     |
|    fps             | 108 |
|    iterations      | 1   |
|    time_elapsed    | 4   |
|    total_timesteps | 512 |
----------------------------
-----------------------------------------
| time/                   |             |
|    fps                  | 120         |
|    iterations           | 2           |
|    time_elapsed         | 8           |
|    total_timesteps      | 1024        |
| train/                  |             |
|    approx_kl            | 0.015572818 |
|    clip_fraction        | 0.197       |
|    clip_range           | 0.211       |
|    entropy_loss         | -1.08       |
|    explained_variance   | -0.012      |
|    learning_rate        | 0.000993    |
|    loss                 | 0.169       |
|    n_updates            | 6           |
|    policy_gradient_loss | -0.0299     |
|    value_loss           | 0.9

## Trading Blotter 

In [16]:
INITIAL_CASH = 10_000_000  # $10 million

def preprocess_data(df):
    df['liquidity'] = df['bid_sz_00'] * df['bid_px_00'] + df['ask_sz_00'] * df['ask_px_00']
    return df

def calculate_rsi(data, window=14):
    delta = data.diff()
    gain = (delta.where(delta > 0, 0)).rolling(window=window).mean()
    loss = (-delta.where(delta < 0, 0)).rolling(window=window).mean()
    rs = gain / loss
    rsi = 100 - (100 / (1 + rs))
    return rsi

def calculate_vol_and_liquidity(price_df, volume_df, window_size):
    # Calculate rolling statistics
    rolling_mean_vol = price_df.pct_change().rolling(window=window_size).mean()
    rolling_std_vol = price_df.pct_change().rolling(window=window_size).std()
    rolling_mean_liq = volume_df.rolling(window=window_size).mean()
    rolling_std_liq = volume_df.rolling(window=window_size).std()
    
    return rolling_mean_vol, rolling_std_vol, rolling_mean_liq, rolling_std_liq

def get_percentile(current_value, mean, std):
    if std > 0:
        z_score = (current_value - mean) / std
        percentile = norm.cdf(z_score)
    else:
        percentile = 0.5  # No variation
    return percentile

def get_trade_price(base_price, current_vol, current_liq, mean_vol, std_vol, mean_liq, std_liq, trade_direction):
    vol_percentile = get_percentile(current_vol, mean_vol, std_vol)
    liq_percentile = get_percentile(current_liq, mean_liq, std_liq)

    # Define price adjustment scenarios based on market conditions
    if vol_percentile >= 0.9 and liq_percentile < 0.1:
        price_adjustment_percent = np.random.uniform(-0.25, -0.15)
    elif vol_percentile <= 0.1 and liq_percentile < 0.1:
        price_adjustment_percent = np.random.uniform(-0.10, -0.05)
    elif vol_percentile >= 0.9 and liq_percentile >= 0.9:
        price_adjustment_percent = np.random.uniform(-0.05, +0.10)
    else:
        price_adjustment_percent = np.random.uniform(-0.05, +0.05)  # Default for normal conditions

    # Adjust price based on trade direction
    if trade_direction == 'BUY':
        adjusted_price = base_price * (1 - price_adjustment_percent)
    else:  # SELL
        adjusted_price = base_price * (1 + price_adjustment_percent)
    
    return adjusted_price


In [17]:
class TradingEnvironmentwithBlotter:
    def __init__(self, data, daily_trading_limit, window_size):
        self.data = preprocess_data(data)
        self.daily_trading_limit = daily_trading_limit
        self.window_size = window_size
        self.state_columns = ['price', 'liquidity', 'RSI', 'MACD', 'MACD_signal', 'MACD_hist', 'Stoch_k', 'Stoch_d',
                              'OBV', 'Upper_BB', 'Middle_BB', 'Lower_BB', 'ATR_1', 'ADX', '+DI', '-DI', 'CCI']
        self.reset()

    def reset(self):
        self.current_step = 0
        self.balance = INITIAL_CASH
        self.shares_held = 0
        self.total_shares_traded = 0
        self.cumulative_reward = 0
        self.trades = []
        self.portfolio = {'cash': self.balance, 'holdings': {ticker: 0 for ticker in self.data['symbol'].unique()}}
        self.data['RSI'] = calculate_rsi(self.data['price'])
        self.data['pct_change'] = self.data['price'].pct_change()
        self.data['rolling_mean_vol'], self.data['rolling_std_vol'], self.data['rolling_mean_liq'], self.data['rolling_std_liq'] = calculate_vol_and_liquidity(self.data['price'], self.data['liquidity'], self.window_size)

    def step(self):
        row = self.data.iloc[self.current_step]
        current_price = row['price']
        current_time = pd.to_datetime(row['ts_event'])
        current_rsi = row['RSI']
        current_vol = row['pct_change']
        current_liq = row['liquidity']
        mean_vol = row['rolling_mean_vol']
        std_vol = row['rolling_std_vol']
        mean_liq = row['rolling_mean_liq']
        std_liq = row['rolling_std_liq']

        if current_rsi < 30:  # Entry signal based on RSI
            trade_direction = 'BUY'
            trade_price = get_trade_price(current_price, current_vol, current_liq, mean_vol, std_vol, mean_liq, std_liq, trade_direction)
            trade_size = (self.portfolio['cash'] * np.random.uniform(0.001, 0.005)) / trade_price
            if self.portfolio['cash'] >= trade_size * trade_price:
                self.portfolio['cash'] -= trade_size * trade_price
                self.portfolio['holdings'][row['symbol']] += trade_size
                trade_status = 'filled'
            else:
                trade_status = 'cancelled'
        elif current_rsi > 70:  # Exit signal based on RSI
            trade_direction = 'SELL'
            if self.portfolio['holdings'][row['symbol']] > 0:
                trade_size = min(self.portfolio['holdings'][row['symbol']], self.portfolio['cash']*np.random.uniform(0.001, 0.005) / current_price)
                trade_price = get_trade_price(current_price, current_vol, current_liq, mean_vol, std_vol, mean_liq, std_liq, trade_direction)
                self.portfolio['cash'] += trade_size * trade_price
                self.portfolio['holdings'][row['symbol']] -= trade_size
                trade_status = 'filled'
            else:
                trade_size = 0
                trade_status = 'cancelled'
        else:
            trade_direction = 'HOLD'
            trade_size = 0
            trade_price = current_price
            trade_status = 'skipped'

        if trade_size > 0:
            expected_price = row['ask_px_00']
            actual_price = row['price']
            transaction_time = row['ts_in_delta']
            transaction_cost = self._calculate_transaction_cost(row['Volume'], 0.3, self.data['Volume'].mean())
            slippage = expected_price - actual_price
            time_penalty = 1000 * transaction_time / 1e9
            reward = - (slippage + time_penalty + transaction_cost)
        
            self.cumulative_reward += reward
            self.trades.append({
                'step': self.current_step,
                'timestamp': current_time,
                'action': trade_direction,
                'price': trade_price,
                'shares': trade_size,
                'symbol': row['symbol'],
                'reward': reward,
                'transaction_cost': transaction_cost,
                'slippage': slippage,
                'time_penalty': time_penalty
            })

            

        self.current_step += 1
        if self.current_step >= len(self.data) - 1:
            done=True
            self.current_step = 0

    def _calculate_transaction_cost(self, volume, volatility, daily_volume):
        return volatility * np.sqrt(volume / daily_volume)

    def run(self):
        self.reset()
        for _ in range(len(self.data)):
            self.step()
        return self.cumulative_reward, self.trades

    def render(self):
        print(f'Cumulative reward: {self.cumulative_reward}')
        row = self.data.iloc[self.current_step]
        print(f'Total portfolio value: {self.portfolio["cash"] + self.portfolio["holdings"][row["symbol"]]*row["Close"]}')
        # get trades in a pandas dataframe
        trades_df = pd.DataFrame(self.trades)
        # Save a csv
        trades_df.to_csv(r'/Users/priyankasahoo/Documents/trades_blotter.csv', index=False)
        for trade in self.trades:
            print(f"Step: {trade['step']}, Timestamp: {trade['timestamp']}, Action: {trade['action']}, Price: {trade['price']}, Shares: {trade['shares']}, Symbol: {trade['symbol']}, Reward: {trade['reward']}, Transaction Cost: {trade['transaction_cost']}, Slippage: {trade['slippage']}, Time Penalty: {trade['time_penalty']}")

In [18]:
# Filter data for the specified ticker
ticker = 'AAPL'  # Specify the ticker you want to trade
ticker_data = market_features_df[market_features_df['symbol'] == ticker]

window_size = 60
daily_trading_limit = 1000
# Create the trading environment
env = TradingEnvironmentwithBlotter(ticker_data, daily_trading_limit=1000, window_size=window_size)  # Daily trading limit of 1000 shares

# Run the environment
cumulative_reward, trades = env.run()

# Render the results
env.render()

Cumulative reward: -12231.516067279417
Total portfolio value: 10011585.059077919
Step: 105, Timestamp: 2023-07-03 08:05:13.717864037, Action: BUY, Price: 194.1373465636911, Shares: 256.15006779499356, Symbol: AAPL, Reward: -0.38225036012723784, Transaction Cost: 0.08423636012724241, Slippage: 0.12999999999999545, Time Penalty: 0.168014
Step: 124, Timestamp: 2023-07-03 08:05:50.024437448, Action: SELL, Price: 197.77354671790133, Shares: 210.33283636785492, Symbol: AAPL, Reward: -0.27620100928928953, Transaction Cost: 0.07183700928926906, Slippage: 0.040000000000020464, Time Penalty: 0.164364
Step: 134, Timestamp: 2023-07-03 08:06:13.187564319, Action: BUY, Price: 197.09180536187904, Shares: 63.16595639851396, Symbol: AAPL, Reward: -0.2850712182043049, Transaction Cost: 0.025398218204301576, Slippage: 0.09000000000000341, Time Penalty: 0.169673
Step: 135, Timestamp: 2023-07-03 08:06:13.187564319, Action: BUY, Price: 199.60805158684772, Shares: 66.06316810683052, Symbol: AAPL, Reward: -0.